In [1]:
from mmdet.apis import init_detector, inference_detector, async_inference_detector
from mmdet.utils import register_all_modules
import torch
import torchvision.transforms as transforms
from PIL import Image
import mmcv
import numpy as np
import os
import glob
import xmltodict
from mmengine.fileio import list_from_file

# 指定模型的配置文件和 checkpoint 文件路径
config_file = 'configs/yolo/yolov3_mobilenetv2_8xb24-ms-416-300e_coco.py'
checkpoint_file = 'work_dirs/yolov3_mobilenetv2_pretrained/best_pascal_voc_mAP_epoch_27.pth'
class_dict = {
    'aeroplane': 0,
    'bicycle': 1,
    'bird': 2,
    'boat': 3,
    'bottle': 4,
    'bus': 5,
    'car': 6,
    'cat': 7,
    'chair': 8,
    'cow': 9,
    'diningtable': 10,
    'dog': 11,
    'horse': 12,
    'motorbike': 13,
    'person': 14,
    'pottedplant': 15,
    'sheep': 16,
    'sofa': 17,
    'train': 18,
    'tvmonitor': 19
}

#Register all modules in mmdet into the registries
register_all_modules()
# 若检测到有GPU则使用GPU
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device = torch.device("cpu")

# 根据配置文件和 checkpoint 文件构建模型
model = init_detector(config_file, checkpoint_file, device=device)
model.eval()

# 指定要遍历的文件夹路径
img_ids = list_from_file("../data/VOCdevkit/VOC2007/ImageSets/Main/test.txt")

raw_det_results, raw_annotations = [], []
# 遍历所有的jpg文件
for img_id in img_ids:

    img_path = os.path.join('../data/VOCdevkit/VOC2007/JPEGImages/', img_id + '.jpg')
    # 获取预测结果
    img = mmcv.imread(img_path, channel_order='rgb')
    output2 = inference_detector(model, img)
    print(output2)
    break

    pred_bboxes = output2.pred_instances.bboxes.cpu().numpy()
    pred_scores = output2.pred_instances.scores.cpu().numpy()
    pred_labels = output2.pred_instances.labels.cpu().numpy()
    dets = []
    for label in range(len(class_dict)):
        index = np.where(pred_labels == label)[0]
        pred_bbox_scores = np.hstack(
            [pred_bboxes[index], pred_scores[index].reshape((-1, 1))])
        dets.append(pred_bbox_scores)
    
    raw_det_results.append(dets)
    
    # 解析XML文件
    ann_path = os.path.join('../data/VOCdevkit/VOC2007/Annotations/', img_id + '.xml')
    with open(ann_path) as f:
        xml_data = xmltodict.parse(f.read())

    bboxes, labels = [], []
    obj = xml_data['annotation']['object']
    if type(obj) == list:
        for i in range(len(obj)):
            bboxes.append([int(obj[i]['bndbox']['xmin'])-1, int(obj[i]['bndbox']['ymin'])-1, 
                           int(obj[i]['bndbox']['xmax'])-1, int(obj[i]['bndbox']['ymax'])-1])
            labels.append(class_dict[obj[i]['name']])
    else:
        bboxes.append([int(obj['bndbox']['xmin'])-1, int(obj['bndbox']['ymin'])-1, 
                       int(obj['bndbox']['xmax'])-1, int(obj['bndbox']['ymax'])-1])
        labels.append(class_dict[obj['name']])

    bboxes = torch.tensor(bboxes).cpu().numpy().astype(np.float32)
    labels = torch.tensor(labels).cpu().numpy()

    ann = {'bboxes': bboxes,
           'labels': labels,
           'bboxes_ignore': torch.empty(size=(0,4)).cpu().numpy(),
           'labels_ignore': torch.empty(dtype=torch.int64, size=(0,)).cpu().numpy()}
    raw_annotations.append(ann)

print(raw_det_results)
print(raw_annotations)


Loads checkpoint by local backend from path: work_dirs/yolov3_mobilenetv2_pretrained/best_pascal_voc_mAP_epoch_27.pth
<DetDataSample(

    META INFORMATION
    img_path: None
    scale_factor: (0.4475920679886686, 0.448)
    ori_shape: (500, 353)
    batch_input_shape: (224, 160)
    img_id: 0
    img_shape: (224, 158)
    pad_shape: (224, 160)

    DATA FIELDS
    pred_instances: <InstanceData(
        
            META INFORMATION
        
            DATA FIELDS
            labels: tensor([14, 11,  7])
            bboxes: tensor([[  1.4124,   2.3510, 347.7869, 496.0396],
                        [ 63.7587, 245.1837, 171.3031, 365.1945],
                        [ 63.7587, 245.1837, 171.3031, 365.1945]])
            scores: tensor([0.9992, 0.6674, 0.3348])
        ) at 0x7ff0601ab280>
    gt_instances: <InstanceData(
        
            META INFORMATION
        
            DATA FIELDS
            labels: tensor([], dtype=torch.int64)
            bboxes: tensor([], size=(0, 4))
      

In [2]:
from mmdet.apis import init_detector, inference_detector, async_inference_detector
from mmdet.utils import register_all_modules
import torch
import torchvision.transforms as transforms
from PIL import Image
import mmcv
import numpy as np
import os
import glob
import xmltodict
from mmdet.datasets.voc import VOCDataset
from mmengine.fileio import list_from_file

# 指定模型的配置文件和 checkpoint 文件路径
config_file = 'configs/yolo/yolov3_mobilenetv2_8xb24-ms-416-300e_coco.py'
checkpoint_file = 'work_dirs/yolov3_mobilenetv2_pretrained/best_pascal_voc_mAP_epoch_27.pth'
class_dict = {
    'aeroplane': 0,
    'bicycle': 1,
    'bird': 2,
    'boat': 3,
    'bottle': 4,
    'bus': 5,
    'car': 6,
    'cat': 7,
    'chair': 8,
    'cow': 9,
    'diningtable': 10,
    'dog': 11,
    'horse': 12,
    'motorbike': 13,
    'person': 14,
    'pottedplant': 15,
    'sheep': 16,
    'sofa': 17,
    'train': 18,
    'tvmonitor': 19
}

#Register all modules in mmdet into the registries
register_all_modules()
# 若检测到有GPU则使用GPU
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device = torch.device("cpu")

# 根据配置文件和 checkpoint 文件构建模型
model = init_detector(config_file, checkpoint_file, device=device)
model.eval()

test_pipeline = [
    dict(type='LoadImageFromFile'),
    dict(type='Resize', scale=(224, 224), keep_ratio=True),
    # avoid bboxes being resized
    dict(type='LoadAnnotations', with_bbox=True),
    dict(
        type='PackDetInputs',
        meta_keys=('img_id', 'img_path', 'ori_shape', 'img_shape',
                   'scale_factor'))
]

data = VOCDataset(ann_file='../data/VOCdevkit/VOC2007/ImageSets/Main/test.txt',
        img_subdir='../data/VOCdevkit/VOC2007/test_img/',
        ann_subdir='../data/VOCdevkit/VOC2007/Annotations/',
        test_mode=True,
        pipeline=test_pipeline)

# 指定要遍历的文件夹路径
img_ids = list_from_file("../data/VOCdevkit/VOC2007/ImageSets/Main/test.txt")

voc_annotations, voc_det_results  = [], []
for i in range(len(data)):

    ann = {'bboxes': data[i]['data_samples'].gt_instances.bboxes.cpu().numpy(),
           'labels': data[i]['data_samples'].gt_instances.labels.cpu().numpy(),
           'bboxes_ignore': data[i]['data_samples'].ignored_instances.bboxes.cpu().numpy(),
           'labels_ignore': data[i]['data_samples'].ignored_instances.labels.cpu().numpy()}
    voc_annotations.append(ann)

    img_path = os.path.join('../data/VOCdevkit/VOC2007/JPEGImages/', img_ids[i] + '.jpg')
    # 获取预测结果
    img = mmcv.imread(img_path, channel_order='rgb')
    output2 = inference_detector(model, img)

    pred_bboxes = output2.pred_instances.bboxes.cpu().numpy()
    pred_scores = output2.pred_instances.scores.cpu().numpy()
    pred_labels = output2.pred_instances.labels.cpu().numpy()
    dets = []
    for label in range(len(class_dict)):
        index = np.where(pred_labels == label)[0]
        pred_bbox_scores = np.hstack(
            [pred_bboxes[index], pred_scores[index].reshape((-1, 1))])
        dets.append(pred_bbox_scores)
    
    voc_det_results.append(dets)


print(voc_det_results)
print(voc_annotations)


Loads checkpoint by local backend from path: work_dirs/yolov3_mobilenetv2_pretrained/best_pascal_voc_mAP_epoch_27.pth
[[array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([[6.3758656e+01, 2.4518375e+02, 1.7130309e+02, 3.6519455e+02,
        3.3476356e-01]], dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([[ 63.758656  , 245.18375   , 171.30309   , 365.19455   ,
          0.66736794]], dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([[  1.4124005,   2.3509946, 347.7869   , 496.0396   ,   0.999199 ]],
      dtype=float32), array([], shape=(0, 5), dtype=float32), array([], shape=(0, 5), dtype=float32), array([], 

In [ ]:
for i in range(len(raw_annotations)):
    if not np.array_equal(raw_annotations[i]['bboxes'], voc_annotations[i]['bboxes']) or \
       not np.array_equal(raw_annotations[i]['labels'], voc_annotations[i]['labels']):
        print(i)